In [36]:
import glob
import re
import os
import time
from collections import Counter, defaultdict
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import bokeh.plotting
import bokeh.io

bokeh.io.output_notebook()

Loading BokehJS ...

In [ ]:
file_list = glob.glob('Data/Kmer_stats/*/Chromosomes/kmers_4/*.csv.gz')

In [ ]:
file_list[0]

In [ ]:
len(file_list)

In [ ]:
dfs = [pd.read_csv(f) for f in file_list]

In [ ]:
len(dfs)

In [ ]:
df1 = dfs[0].copy()[dfs[0]['E_values'] < 0.001].sort_values('Z_score').reset_index(drop=True)

In [ ]:
df1

In [ ]:
df1['Rank'] = df1['Z_score'].rank().astype(int)

In [ ]:
df1

In [ ]:
plot_data = df1[['kmer','Observed']].sort_values('Observed')

In [ ]:
x = plot_data['kmer']
y = plot_data['Observed'].values

In [ ]:
y

In [ ]:
plt.plot(x, y)
plt.show()

In [ ]:
plt.figure(figsize=(60, 15))

plt.subplot(131)
plt.bar(x, y)
plt.xticks(rotation=90)
plt.show()

In [ ]:
df2 = dfs[0].copy().sort_values('Z_score').reset_index(drop=True)

In [ ]:
df2['diff'] = df2['Observed'] - df2['Expected']
df2

In [ ]:
import numba

In [ ]:
@numba.jit(nopython=True)
def get_gc_content(sequence):
    """
    Finction to calculate the the gc content of a sequence.
    
    Inputs:
    
        sequence - a string representing a DNA sequence.
    
    Outputs:
    
        gc - a float representing the of (g + c) content of a sequence.
    
    """
    # get the sequence length and 
    # make all the sequence characters upper case
    seq_len = len(sequence)
    if not sequence:
        return 0.0
    # count all gs and cs
    c = sequence.count('C')
    g = sequence.count('G')
    # returns the gc content from a sequence
    # sum up the |Gs and Cs counts and divide 
    # by the sequence length
    return round((c + g) / seq_len, 4)

In [3]:
from fasta_parser import parse_fasta

In [4]:
for name, seq in parse_fasta('Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000016725.1_chr.fna.gz'):
    sequence = seq

In [4]:
for name, seq in parse_fasta('Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000202835.1_chr.fna.gz'):
    sequence2 = seq

In [5]:
def gc_content(sequence):
    """
    Finction to calculate the the gc content of a sequence.
    
    Inputs:
    
        sequence - a string representing a DNA sequence.
    
    Outputs:
    
        gc - a float representing the of (g + c) content of a sequence.
    
    """
    # get the sequence length and 
    # make all the sequence characters upper case
    seq_len = len(sequence)
    cg = np.sum(np.array([sequence.count(i) for i in 'CG']))
    return Counter(sequence), round((cg / (seq_len)) * 100, 4)

In [96]:
start = time.time()
gc_content(sequence)
end = time.time()
print("Elapsed (no compilation) = %s" % (end - start))

Elapsed (no compilation) = 0.18021774291992188


In [9]:
import numba

In [6]:
%load_ext cython

In [10]:
@numba.jit(nopython=True)
def find_gc(seq: str) -> float:
    """ Calculate GC content """

    if not seq:
        return 0

    gc = 0
    for base in seq.upper():
        if base in ('C', 'G'):
            gc += 1

    return (gc * 100) / len(seq)

In [97]:
start = time.time()
find_gc(sequence)
end = time.time()
print("Elapsed (no compilation) = %s" % (end - start))

Elapsed (no compilation) = 1.1696343421936035


In [98]:
def gc(seq: str) -> float:
    """ Calculate GC content """

    return (seq.upper().count('C') +
            seq.upper().count('G')) * 100 / len(seq) if seq else 0

In [99]:
start = time.time()
gc(sequence)
end = time.time()
print("Elapsed (no compilation) = %s" % (end - start))

Elapsed (no compilation) = 0.0361173152923584


In [100]:
@numba.jit()
def gc_numba(seq: str) -> float:
    """ Calculate GC content """

    return (seq.upper().count('C') +
            seq.upper().count('G')) * 100 / len(seq) if seq else 0

In [101]:
start = time.time()
gc_numba(sequence)
end = time.time()
print("Elapsed (no compilation) = %s" % (end - start))

Elapsed (no compilation) = 0.6156406402587891


In [16]:
def find_gc(seq: str) -> float:
    """ Calculate GC content """

    return len(re.findall('[GC]', seq.upper()) * 100) / len(seq) if seq else 0

In [102]:
%timeit find_gc(sequence)

1.05 s ± 50.4 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [103]:
start = time.time()
find_gc(sequence)
end = time.time()
print("Elapsed (no compilation) = %s" % (end - start))

Elapsed (no compilation) = 1.1169109344482422


In [19]:
 %reload_ext cython

In [7]:
%%cython
def gc_cython(str string):
    cdef int N = len(string)
    cdef str bases = 'GC'
    cdef float gc = 0.0 
    for base in string.upper():
        if base in bases:
            gc += 1.0
    return (gc / N)

In [8]:
gc = pd.Series(gc_cython(sequence) * 100, index = ["GC"]).reset_index()
df_gc = pd.DataFrame(gc).rename(columns={'index': 'bases', 0: 'counts'})

In [9]:
df_gc

bases     counts
0    GC  67.992729

In [10]:
gc1 = pd.Series(gc_cython(sequence2) * 100, index = ["GC"]).reset_index()
df_gc1 = pd.DataFrame(gc1).rename(columns={'index': 'bases', 0: 'counts'})
df_gc1

bases     counts
0    GC  67.579174

In [11]:
start = time.time()
gc_cython(sequence)
end = time.time()
print("Elapsed (no compilation) = %s" % (end - start))

Elapsed (no compilation) = 0.08029341697692871


In [12]:
%%cython
def count_bases_cython(str string):
    cdef str bases = 'ACGT'
    cdef int a = 0
    cdef int c = 0
    cdef int g = 0
    cdef int t = 0
    for base in string:
        if base == 'A':
            a += 1
        elif base == 'C':
            c += 1
        elif base == 'G':
            g += 1
        else:
            t += 1
    return dict(zip('ACGT', [a, c, g, t]))       

In [13]:
bases = count_bases_cython(sequence)

In [14]:
df = pd.DataFrame(bases.items(), columns=['bases', 'counts'])
df

bases   counts
0     A   540108
1     C  1161260
2     G  1143168
3     T   544691

In [15]:
pd.concat([df, df_gc])

bases        counts
0     A  5.401080e+05
1     C  1.161260e+06
2     G  1.143168e+06
3     T  5.446910e+05
0    GC  6.799273e+01

In [16]:
df2 = pd.DataFrame(count_bases_cython(sequence2).items(), columns=['bases', 'counts'])
pd.concat([df2, df_gc1])

bases        counts
0     A  6.055490e+05
1     C  1.274307e+06
2     G  1.259514e+06
3     T  6.100410e+05
0    GC  6.757917e+01

In [35]:
(5.401080e+05+6.055490e+05)/2, (6.799273e+01 + 6.757917e+01)/2

(572828.5, 67.78595)

In [ ]:
bases,counts
A,572828.0
C,1217783.0
G,1201341.0
T,577366.0
GC,67.7859514951706


In [110]:
start = time.time()
count_bases_cython(sequence)
end = time.time()
print("Elapsed (no compilation) = %s" % (end - start))

Elapsed (no compilation) = 0.044477224349975586


In [30]:
def genome_stats_in_windows(fasta_dict, name, as_overlap=False, k=20):
    """GC Content in a DNA/RNA sub-sequence length k. In
    overlapp windows of lenght k.

    Inputs:

        sequence - a string representing a DNA sequence.
        as_overlap - boolean that represents if overlap is needed.
        k - a integer reppresenting the lengths of overlappig bases.
            Default is 20.

    Outputs:

        gc_content - an array-like object with


    """
    seq = ''
    
    for file in fasta_dict[name]:
        for n, seq in parse_fasta(file):
            # make sequence upper case and getting the length of it
            seq += seq.upper()
    # the array-like object to collect the data
    gc_content = []
    # non overlap sequence length
    non_overlap = range(0, len(seq) - k + 1, k)
    # overlap sequence length
    overlap = range(0, len(seq) - k + 1)
    # overlap is needed
    if as_overlap:
        # iterates to the overlap region
        for i in overlap:
            # creates the substring to count the gc_content
            subseq = seq[i:i + k]
            # count and sum up the Gs and Cs counts
            g_c = gc_cython(subseq)
            # collect the data in the array container
            gc_content.append(round(g_c, 4) * 100)
    # if non overlap is choosed
    else:
        # iterates to the mon overlap region
        for j in non_overlap:
            # creates the substring to count the gc_content
            subseq = seq[j:j + k]
            # count and sum up the Gs and Cs counts
            g_c = gc_cython(subseq)
            # collect the data in the array container
            gc_content.append(round(g_c, 4) * 100)
    return gc_content

In [20]:
from system_utils import get_all_fasta

In [21]:
fasta_dict = get_all_fasta('Data/Genomes_splitted', 'Chromosomes', 'gz')
fasta_dict

defaultdict(list,
            {'Acidiphilium': ['Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000016725.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000202835.1_chr.fna.gz'],
             'Acidipropionibacterium': ['Data/Genomes_splitted/Acidipropionibacterium/Chromosomes/GCF_001441165.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidipropionibacterium/Chromosomes/GCF_005890155.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidipropionibacterium/Chromosomes/GCF_003325455.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidipropionibacterium/Chromosomes/GCF_004011075.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidipropionibacterium/Chromosomes/GCF_900637925.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidipropionibacterium/Chromosomes/GCF_004011055.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidipropionibacterium/Chromosomes/GCF_005890135.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidipropioni

In [13]:
acid = {'Acidiphilium': ['Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000016725.1_chr.fna.gz',
              'Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000202835.1_chr.fna.gz']}

In [31]:
window = genome_stats_in_windows(acid, 'Acidiphilium', as_overlap=False, k=3000)

In [32]:
dfw = pd.DataFrame (window, columns=['GC_window'])
dfw.T

0     1     2     3     4      5     6      7      8      9     \
GC_window  62.7  65.7  66.6  68.3  64.2  68.23  65.6  68.97  67.27  70.47   

           ...  2489   2490   2491   2492   2493   2494  2495   2496  2497  \
GC_window  ...  67.9  67.47  66.07  72.07  68.57  70.93  68.0  66.27  65.7   

            2498  
GC_window  66.23  

[1 rows x 2499 columns]

In [23]:
def gc_count_fasta(fasta_dict, name):
    """
    Function to count all n-grams/k-mers (substrings of lenght n or k) in a
    big string/genome.

    Inputs:
        fasta_dict - a dictionary-like object that map a word/kmer to their value,
                    in this case a full path to the files to be analized.
        name - a string representing a word (key) that represent a key in a
               dictionary.

    Outputs:
        gc content - a float representing the mean of the gc content from all
                     genus/species analyzed.
    """
    # get the number of files in the names directory
    num_fastas = len(fasta_dict[name])
    # initialize the counter
    gc_tot = 0
    # iterates through the list of paths
    for filename in fasta_dict[name]:
        # reads the file and parse the content
        print(f'Reading and parsing the filename {filename}')
        for name, sequence in parse_fasta(filename):
            # add the gc content from all files
            gc_tot += gc_cython(sequence)
    # returns the mean of the gc content from all files
    return (gc_tot / num_fastas) * 100

In [134]:
((67.992729 + 67.579174) / 2) 

67.7859515

In [136]:
gc_count_fasta(acid, 'Acidiphilium')

Reading and parsing the filename Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000016725.1_chr.fna.gz
Reading and parsing the filename Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000202835.1_chr.fna.gz


67.7859514951706

In [24]:
def count_bases_fasta(fasta_dict, name):
    """
    Function to count all n-grams/k-mers (substrings of lenght n or k) in a
    big string/genome.

    Inputs:
        fasta_dict - a dictionary-like object that map a word/kmer to their value,
                    in this case a full path to the files to be analized.
        name - a string representing a word (key) that represent a key in a
               dictionary.

    Outputs:
        final_counter - a dictionary-like mapping the kmers to their calculated count
                        in the input string, from a file.
        seq_length - a integer representing the mean of the lengths from all genomes
                     files in the directory.
    """
    # get the number of files in the names directory
    num_fastas = len(fasta_dict[name])
    print(f'The number of fasta files for this genus is {num_fastas}.')
    # initialize the counter
    counter = Counter()
    # get the sequence length
    seq_len = 0
    num_files = 0
    # iterates through the list of paths
    for filename in fasta_dict[name]:
        # reads the file and parse the content
        print(f'Reading and parsing the file {filename}')
        for name, sequence in parse_fasta(filename):
            print(f'Sequence length {len(sequence)}')
            seq_len += len(sequence)
            # get the counting the kmers
            cnt = count_bases_cython(sequence)
            # add the count of the current file to the counter
            counter.update(cnt)
        num_files += 1
    # to get the mean of the kmer count for all the files
    final_counter = {k: (c // num_fastas) for k, c in counter.items()}
    # get mean of genomes lengths
    seq_length = int(seq_len / num_files)
    return final_counter

In [25]:
count_bases_fasta(acid, 'Acidiphilium')

The number of fasta files for this genus is 2.
Reading and parsing the file Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000016725.1_chr.fna.gz
Sequence length 3389227
Reading and parsing the file Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000202835.1_chr.fna.gz
Sequence length 3749411


{'A': 572828, 'C': 1217783, 'G': 1201341, 'T': 577366}

In [49]:
s = 'AAATTCGAATTTAAATTCGAATTTGCNGC'
p = r'[A|G]AATT[C|T]'
m = re.finditer(p, s)
list(m)

[<re.Match object; span=(0, 6), match='AAATTC'>,
 <re.Match object; span=(6, 12), match='GAATTT'>,
 <re.Match object; span=(12, 18), match='AAATTC'>,
 <re.Match object; span=(18, 24), match='GAATTT'>]

In [41]:
def read_patterns(filename):
    """
    Reads all patterns to search for from a text file.
    
    Inputs:
        filename - a path to the text file where the patterns are 
                   listed one per line.
    
    Outputs:
        re_cuts - a list-like object containing all the files to be
                  searched in a genome/sequence.
    """
    # start the container
    re_cuts = []
    # open the text file
    with open(filename, 'r') as fh:
        # exclude the header
        header = fh.readline()
        # read each line
        for line in fh:
            # clean spaces and split the data and get the pattern
            # that is the first element
            cut = line.strip().split(';')[0]
            # add the pattern to the list
            re_cuts.append(cut)
    return re_cuts

In [42]:
read_patterns('Data/Rstriction_enzymes/RE_cut_sites')

['GACGTC',
 'C[ACGT]{20}G',
 'GGTACC',
 'GT[A|C][G|T]AC',
 'CCGC',
 'AACGTT',
 'CTGAAG[A|C|G|T]{16}',
 'AGCGCT',
 'CTTAAG',
 'AC[A|G][C|T]GT',
 'ACCGGT',
 'GAC[ACGT]{5}GTC',
 'CAC[ACGT]{4}GTG',
 'AGCT',
 'GGATC[A|C|G|T]{4}',
 'CAG[ACGT]{3}CTG',
 'GGGCCC',
 'GTGCAC',
 '[A|G]AATT[C|T]',
 'GGCGCGCC',
 'ATTAAT',
 'GCGATCGC',
 'C[C|T]CG[A|G]G',
 'GG[A|T]CC',
 'CCTAGG',
 'G[G|T]GC[A|C]C',
 '[A|C|G|T]{10}AC[A|C|G|T]{4}GTA[C|T]C[A|C|G|T]{12}',
 'GGATCC',
 'GG[C|T][A|G]CC',
 'G[A|G]GC[C|T]C',
 'GAAGAC[A|C|G|T]{2}',
 'CCTCAGC',
 'GCAGC[A|C|G|T]{8}',
 'CCATC[A|C|G|T]{4}',
 'ACGGC[A|C|G|T]{12}',
 '[A|C|G|T]{12}CGA[A|C|G|T]{6}TGC[A|C|G|T]{12}',
 'GTATCC[A|C|G|T]{6}',
 'TGATCA',
 'CTAG',
 'GCC[A|C|G|T]{5}GGC',
 'AGATCT',
 'GCT[A|C|G|T]{1}AGC',
 'CACGTC',
 'ACTGGG[A|C|G|T]{5}',
 'GCTAGC',
 'CTGGAG[A|C|G|T]{16}',
 'CTTGAG[A|C|G|T]{16}',
 'CCT[A|C|G|T]{1}AGC',
 '[C|T]ACGT[A|G]',
 'GAT[A|C|G|T]{4}ATC',
 'G[A|G]CG[C|T]C',
 'GGTCTC[A|C|G|T]{5}',
 'CC[A|C|G|T]{2}GG',
 '[A|T]CCGG[A|T]',
 '[A|C|G|T]{9}AC[A|C

In [20]:
re_cuts = []

with open('Data/Rstriction_enzymes/RE_cut_sites', 'r') as fh:
    header = fh.readline()
    for line in fh:
        cut = line.strip().split(';')[0]
        re_cuts.append(cut)

re_cuts[:10]

['GACGTC',
 'C[ACGT]{20}G',
 'GGTACC',
 'GT[A|C][G|T]AC',
 'CCGC',
 'AACGTT',
 'CTGAAG[A|C|G|T]{16}',
 'AGCGCT',
 'CTTAAG',
 'AC[A|G][C|T]GT']

In [69]:
defaultdict(list, [(cut, []) for cut in re_cuts])

defaultdict(list,
            {'GACGTC': [],
             'C[ACGT]{20}G': [],
             'GGTACC': [],
             'GT[A|C][G|T]AC': [],
             'CCGC': [],
             'AACGTT': [],
             'CTGAAG[A|C|G|T]{16}': [],
             'AGCGCT': [],
             'CTTAAG': [],
             'AC[A|G][C|T]GT': [],
             'ACCGGT': [],
             'GAC[ACGT]{5}GTC': [],
             'CAC[ACGT]{4}GTG': [],
             'AGCT': [],
             'GGATC[A|C|G|T]{4}': [],
             'CAG[ACGT]{3}CTG': [],
             'GGGCCC': [],
             'GTGCAC': [],
             '[A|G]AATT[C|T]': [],
             'GGCGCGCC': [],
             'ATTAAT': [],
             'GCGATCGC': [],
             'C[C|T]CG[A|G]G': [],
             'GG[A|T]CC': [],
             'CCTAGG': [],
             'G[G|T]GC[A|C]C': [],
             '[A|C|G|T]{10}AC[A|C|G|T]{4}GTA[C|T]C[A|C|G|T]{12}': [],
             'GGATCC': [],
             'GG[C|T][A|G]CC': [],
             'G[A|G]GC[C|T]C': [],
             

In [38]:
def get_files(dir_name):
    # create a list of file and sub directories
    # names in the given directory
    files = os.listdir(dir_name)
    all_files = []
    # Iterate over all the entries
    for entry in files:
        # Create full path
        full_path = os.path.join(dir_name, entry)
        # If entry is a directory then get the list of files in this directory
        if os.path.isdir(full_path):
            all_files += get_files(full_path)
        else:
            all_files.append(full_path)
    return all_files

In [39]:
get_files('Data/Genomes_splitted/')

['Data/Genomes_splitted/Thiomonas/Plasmids/GCF_900634615.1_plas.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Plasmids/GCF_000092605.1_plas.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Plasmids/GCF_002028405.1_plas.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Plasmids/GCF_900634585.1_plas.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Plasmids/GCF_000253115.1_plas.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Plasmids/GCF_900634595.1_plas.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Plasmids/GCF_900634575.1_plas.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Chromosomes/GCF_000092605.1_chr.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Chromosomes/GCF_900634585.1_chr.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Chromosomes/GCF_002028405.1_chr.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Chromosomes/GCF_900634575.1_chr.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Chromosomes/GCF_900634615.1_chr.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Chromosomes/GCF_000253115.1_chr.fna.gz',
 'Data/Genomes_splitted/Thiomonas/Chrom

In [43]:
'Data/Genomes_splitted/Thiomonas/Plasmids/GCF_900634615.1_plas.fna.gz'.split('/')

['Data',
 'Genomes_splitted',
 'Thiomonas',
 'Plasmids',
 'GCF_900634615.1_plas.fna.gz']

In [ ]:
name 

In [70]:
def restriction_sites_regex(sequence, recog_site):
    """
    Find the start indices of restriction sites in a sequence.
    
    Inputs:
        sequence - a string representing a sequence.
        recog_site - a string representing a restriction recognition site.
    
    Outputs:
        a list/array-like object with all start positions from the 
        restriction enzyme recognition site.
    
    EX:
    >> seq = lambda fasta 
    https://www.neb.com/-/media/nebus/page-images/tools-and-resources/interactive-tools/\
    dna-sequences-and-maps/text-documents/lambdafsa.txt
    >> restriction_sites_regex(seq, 'AAGCTT')
     [23129, 25156, 27478, 36894, 37458, 37583, 44140]
     
    >> restriction_sites_regex(seq, 'GAATTC')
    [21528, 26475, 32199, 39726, 45613]
    
    >> restriction_sites_regex(seq, 'GGTACC')
    [17295, 18820]
    
    >> restriction_sites_regex(seq, '')
    -1
    
    >> restriction_sites_regex('', 'GGTACC')
    -1
    """
    # sequence and patter to upper case
    sequence, recog_site = sequence.upper(), recog_site.upper()
    # compile the pattern
    rec_site = re.compile(recog_site)
    # if not find any seq or patter returns -1
    # to keep the python pattern
    if recog_site == '' or sequence == '':
        return -1
    # if found returns a tuple of the site and its start positions
    return [rec.start() for rec in re.finditer(rec_site, sequence)]

In [79]:
def all_re_cut_sites(sequence, cut_sites_list):
    sites = []
    for cut in cut_sites_list:
        p = restriction_sites_regex(sequence, cut)
        if p:
            sites.append((cut, p))
    return sites 

In [80]:
all_re_cut_sites(seq, re_cuts)

[('GACGTC',
  [2822,
   4037,
   4367,
   5890,
   14903,
   15860,
   21849,
   22723,
   26327,
   30614,
   40302,
   40607,
   43201,
   48918,
   49622,
   50632,
   54805,
   58499,
   58841,
   60328,
   60833,
   63725,
   69708,
   73468,
   81447,
   109223,
   114082,
   117838,
   121928,
   123602,
   124647,
   125097,
   125790,
   126018,
   126100,
   126121,
   132732,
   133817,
   139775,
   144216,
   144870,
   147602,
   147827,
   151780,
   159488,
   160111,
   162928,
   163780,
   173177,
   175291,
   186913,
   196243,
   197928,
   204767,
   205327,
   207437,
   215558,
   218846,
   221261,
   224430,
   231918,
   235762,
   241897,
   245391,
   246547,
   250703,
   261981,
   266627,
   267045,
   269086,
   278879,
   279095,
   279452,
   282710,
   283739,
   291453,
   291726,
   293948,
   297521,
   298590,
   308336,
   310284,
   310939,
   311197,
   313300,
   313370,
   314985,
   315653,
   318924,
   320897,
   350774,
   354739,
   35

In [77]:
pd.DataFrame(sites, columns=['site', 'positions'])

site                                          positions
0                GACGTC  [2822, 4037, 4367, 5890, 14903, 15860, 21849, ...
1          C[ACGT]{20}G  [56, 81, 104, 131, 166, 206, 228, 259, 297, 33...
2                GGTACC  [13969, 14371, 43477, 46835, 47575, 59005, 680...
3        GT[A|C][G|T]AC  [1913, 1991, 3938, 7751, 9302, 9681, 16001, 19...
4                  CCGC  [403, 472, 519, 627, 642, 648, 658, 692, 701, ...
..                  ...                                                ...
232  CCA[A|C|G|T]{9}TGG  [2121, 2538, 4587, 10673, 12997, 16601, 20709,...
233              CTCGAG  [1370, 3270, 4127, 6718, 8861, 26346, 27983, 3...
234              CCCGGG  [7403, 8123, 12523, 15407, 17632, 18073, 18701...
235  GAA[A|C|G|T]{4}TTC  [739, 2695, 2936, 4483, 7275, 7447, 9433, 1368...
236              GACGTC  [2822, 4037, 4367, 5890, 14903, 15860, 21849, ...

[237 rows x 2 columns]

In [64]:
df.index

RangeIndex(start=0, stop=1, step=1)

In [9]:
restriction_sites_regex(sequence, 'C[ACGT]{20}G')

('C[ACGT]{20}G',
 [56,
  81,
  104,
  131,
  166,
  206,
  228,
  259,
  297,
  331,
  358,
  391,
  419,
  442,
  464,
  496,
  526,
  556,
  593,
  634,
  658,
  682,
  704,
  738,
  760,
  784,
  806,
  835,
  862,
  886,
  937,
  961,
  983,
  1012,
  1054,
  1084,
  1108,
  1131,
  1153,
  1186,
  1210,
  1234,
  1296,
  1322,
  1345,
  1369,
  1394,
  1417,
  1453,
  1477,
  1503,
  1531,
  1553,
  1597,
  1619,
  1658,
  1682,
  1710,
  1732,
  1758,
  1781,
  1804,
  1832,
  1858,
  1880,
  1908,
  1931,
  1955,
  1979,
  2012,
  2034,
  2057,
  2085,
  2113,
  2136,
  2164,
  2201,
  2226,
  2249,
  2284,
  2316,
  2342,
  2370,
  2399,
  2435,
  2459,
  2497,
  2531,
  2555,
  2592,
  2614,
  2667,
  2700,
  2771,
  2796,
  2819,
  2844,
  2866,
  2918,
  2942,
  2984,
  3014,
  3046,
  3082,
  3108,
  3141,
  3171,
  3200,
  3223,
  3259,
  3283,
  3305,
  3346,
  3373,
  3401,
  3435,
  3468,
  3493,
  3524,
  3553,
  3585,
  3632,
  3656,
  3703,
  3726,
  3761,
  3785,
  

In [10]:
for site in re_cuts:
    print(restriction_sites_regex(sequence, site))

('GACGTC', [2822, 4037, 4367, 5890, 14903, 15860, 21849, 22723, 26327, 30614, 40302, 40607, 43201, 48918, 49622, 50632, 54805, 58499, 58841, 60328, 60833, 63725, 69708, 73468, 81447, 109223, 114082, 117838, 121928, 123602, 124647, 125097, 125790, 126018, 126100, 126121, 132732, 133817, 139775, 144216, 144870, 147602, 147827, 151780, 159488, 160111, 162928, 163780, 173177, 175291, 186913, 196243, 197928, 204767, 205327, 207437, 215558, 218846, 221261, 224430, 231918, 235762, 241897, 245391, 246547, 250703, 261981, 266627, 267045, 269086, 278879, 279095, 279452, 282710, 283739, 291453, 291726, 293948, 297521, 298590, 308336, 310284, 310939, 311197, 313300, 313370, 314985, 315653, 318924, 320897, 350774, 354739, 355071, 355642, 373674, 375290, 375653, 383246, 388753, 388827, 394578, 398566, 403163, 404624, 410709, 411738, 413330, 417968, 423759, 424349, 429387, 430477, 432613, 434238, 443228, 444092, 445922, 447118, 448616, 448778, 450218, 452537, 455370, 457116, 460848, 462969, 464762, 4

('CAC[ACGT]{4}GTG', [3788, 22049, 22235, 28584, 31227, 38854, 43111, 50524, 57663, 66427, 66565, 72461, 73488, 75016, 80279, 80546, 95545, 99191, 102667, 106300, 109403, 114706, 124091, 136649, 142571, 147691, 148237, 151087, 152608, 158072, 158507, 172095, 176820, 198694, 199762, 201103, 206840, 208251, 208401, 212794, 213010, 227107, 230626, 230984, 232749, 235623, 242356, 246849, 247160, 249009, 255173, 257595, 265978, 269859, 273074, 283448, 284339, 285646, 286311, 292503, 301156, 310061, 310250, 310546, 314791, 315425, 316574, 319175, 330828, 330982, 333098, 337746, 338673, 338859, 339777, 351116, 351309, 356227, 358749, 360197, 362862, 370830, 378723, 382772, 387320, 394148, 400926, 404279, 408751, 414968, 421595, 424522, 429675, 429840, 432768, 446618, 449276, 451012, 504433, 511908, 521330, 527850, 531164, 532301, 537155, 538785, 539110, 543413, 543852, 544404, 548998, 556466, 556899, 557535, 557939, 565627, 568720, 582122, 584120, 584283, 584844, 599549, 601567, 602410, 609413

('GG[A|T]CC', [567, 1123, 1945, 3111, 3220, 3568, 4297, 5448, 6078, 6523, 7623, 8013, 8217, 8752, 9066, 9151, 11271, 11661, 11988, 12310, 13038, 13790, 13909, 15880, 16039, 16409, 16570, 16699, 17629, 17720, 18005, 18044, 20641, 21458, 21509, 21680, 22265, 23257, 23505, 25052, 26356, 26476, 28298, 29459, 30107, 30992, 31222, 31376, 32226, 34437, 34551, 34680, 34761, 35021, 35958, 36758, 36807, 39201, 39654, 39725, 39787, 39831, 40768, 41354, 41960, 42176, 43028, 43262, 43415, 44418, 45267, 45628, 45802, 45845, 46406, 46585, 46854, 47870, 49307, 50574, 50604, 51054, 51668, 53187, 53937, 55152, 55335, 55946, 56075, 57458, 58709, 59155, 59560, 59739, 59914, 60283, 60297, 60864, 61244, 61293, 61513, 61670, 62234, 63247, 65210, 66274, 68234, 68385, 68857, 69083, 69218, 70635, 70908, 71451, 71658, 71822, 72359, 72951, 75221, 77591, 78224, 79304, 79728, 81355, 82030, 82833, 82990, 84685, 85307, 85404, 85646, 87594, 87723, 88482, 90623, 90796, 91366, 91588, 91748, 92242, 92275, 92471, 93262, 9

('GG[C|T][A|G]CC', [90, 581, 1904, 2081, 2267, 2273, 3210, 4529, 4591, 4811, 4937, 5243, 5365, 5392, 5538, 5675, 5956, 6171, 6550, 6646, 6952, 7056, 7602, 7759, 8138, 8252, 8284, 8300, 8434, 8726, 8734, 10328, 11480, 11732, 12220, 12255, 12407, 12811, 13230, 13700, 13969, 13986, 14220, 14371, 15104, 15506, 15845, 15896, 16712, 17082, 17191, 17929, 18710, 18756, 19854, 19876, 20231, 20705, 20777, 21011, 21170, 21402, 21419, 22233, 22338, 22344, 24392, 25029, 25889, 26245, 27539, 27611, 28169, 28192, 29114, 29645, 29804, 29827, 29855, 29978, 30053, 30372, 30518, 31330, 31357, 32816, 32999, 33066, 33120, 33210, 33665, 33733, 33843, 34507, 34788, 34810, 35059, 35226, 35401, 35568, 35820, 35992, 36280, 36612, 36686, 36836, 36930, 37298, 37623, 37839, 37928, 38654, 38699, 38797, 38824, 38924, 39106, 39631, 39838, 40159, 40185, 40198, 40371, 40535, 40824, 40871, 42135, 42544, 42735, 42905, 43236, 43467, 43477, 43890, 44047, 44334, 44340, 44391, 45094, 45448, 45695, 45821, 46031, 46160, 46642,

('[A|C|G|T]{12}CGA[A|C|G|T]{6}TGC[A|C|G|T]{12}', [1168, 5119, 5583, 10525, 10567, 11406, 11888, 13150, 16451, 16929, 17508, 18640, 18787, 20452, 20926, 21856, 22262, 23393, 24463, 24926, 26276, 28009, 28165, 31665, 33025, 34512, 36209, 37898, 37950, 41258, 41612, 43264, 47897, 48426, 50191, 53699, 55817, 56814, 58432, 59248, 59632, 59683, 60099, 60549, 61466, 62282, 62494, 63013, 63184, 63346, 64383, 65263, 67311, 67934, 67979, 68460, 68740, 69352, 71460, 71866, 74914, 76486, 76552, 76859, 77984, 78169, 78441, 78924, 79684, 79966, 80143, 82579, 84715, 85087, 86078, 86780, 87355, 88743, 90503, 93747, 96736, 97991, 98330, 98527, 100598, 101368, 101605, 101857, 103218, 104777, 105296, 112168, 115865, 116829, 118671, 120172, 122120, 123053, 123197, 123715, 123871, 123907, 124141, 127410, 127981, 129452, 131683, 133822, 135079, 136132, 137275, 139193, 140225, 140699, 141011, 141445, 141970, 142679, 142715, 142973, 147268, 148472, 148893, 150265, 150633, 152184, 152268, 153279, 154871, 15739

('CCT[A|C|G|T]{1}AGC', [10122, 13056, 41086, 92663, 92937, 97889, 103485, 113934, 121531, 128620, 130789, 133238, 152650, 155237, 166348, 180420, 191957, 193043, 197040, 212302, 222413, 234699, 250617, 268826, 308001, 319637, 325222, 332714, 334844, 335095, 338644, 357357, 362511, 362541, 363488, 374254, 377501, 381329, 416623, 432126, 433595, 435780, 447086, 451548, 453710, 461434, 478555, 484529, 487471, 488771, 493502, 495870, 503727, 505089, 512424, 513527, 518443, 531560, 542229, 546441, 547062, 566698, 571386, 573737, 579699, 583463, 586857, 607286, 630105, 636357, 643091, 645208, 649424, 652048, 657653, 669566, 672373, 697437, 705781, 722667, 743687, 747208, 766034, 768657, 768905, 775142, 786946, 787854, 848054, 850630, 860854, 865826, 885980, 887336, 890367, 892244, 893542, 909498, 918963, 920399, 956016, 965049, 970510, 1004337, 1011364, 1015380, 1037363, 1052070, 1064671, 1072416, 1100085, 1117473, 1136561, 1140126, 1149878, 1155185, 1163050, 1174964, 1180242, 1180812, 12247

('[A|C|G|T]{9}AC[A|C|G|T]{5}CTCC[A|C|G|T]{10}', [287, 1611, 8190, 12387, 16205, 20122, 21640, 24121, 28275, 39866, 57887, 71300, 79862, 80016, 90958, 91900, 114949, 132365, 142009, 143228, 143305, 143692, 159007, 162281, 162519, 164580, 177752, 178083, 178314, 189760, 192395, 195323, 204366, 204474, 206902, 210438, 221449, 221689, 230799, 240650, 247854, 250449, 251660, 259911, 259971, 288424, 318322, 319239, 321114, 322766, 324433, 332011, 336692, 342348, 346357, 364541, 370490, 378575, 380138, 384422, 388676, 389413, 393431, 393532, 394315, 394855, 403152, 407294, 408196, 408918, 416295, 419166, 421966, 422776, 430841, 431411, 443656, 466103, 471864, 474816, 479444, 485218, 506674, 507277, 510515, 516898, 517479, 517677, 521710, 525383, 529668, 529962, 538787, 543743, 556982, 576358, 584597, 590452, 597636, 613366, 630221, 630824, 631558, 635375, 636271, 637114, 639280, 642112, 650809, 657373, 669127, 682936, 695601, 705487, 708735, 709275, 709461, 709872, 727662, 728091, 729746, 744

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [32]:
def count_bases_fasta(fasta_dict, name, rec_sites):
    """
    Function to count all n-grams/k-mers (substrings of lenght n or k) in a
    big string/genome.

    Inputs:
        fasta_dict - a dictionary-like object that map a word/kmer to their value,
                    in this case a full path to the files to be analized.
        name - a string representing a word (key) that represent a key in a
               dictionary.

    Outputs:
        final_counter - a dictionary-like mapping the kmers to their calculated count
                        in the input string, from a file.
        seq_length - a integer representing the mean of the lengths from all genomes
                     files in the directory.
    """
    # get the number of files in the names directory
    num_fastas = len(fasta_dict[name])
    print(f'The number of fasta files for this genus is {num_fastas}.')
    # initialize the counter
    rec_sites_found = defaultdict(list)
    # iterates through the list of paths
    for filename in fasta_dict[name]:
        # reads the file and parse the content
        print(f'Reading and parsing the file {filename}')
        for name, sequence in parse_fasta(filename):
            for site in rec_sites:
                resite = restriction_sites_regex(sequence, site)[1]
                rec_sites_found[site] += resite
    return rec_sites_found

In [33]:
re_sites = count_bases_fasta(acid, 'Acidiphilium', re_cuts)

The number of fasta files for this genus is 2.
Reading and parsing the file Data/Genomes_splitted/Acidiphilium/Chromosomes/GCF_000016725.1_chr.fna.gz


ValueError: operands could not be broadcast together with shapes (0,) (916,) 

In [31]:
len(re_sites), len(re_cuts)

(221, 242)

In [82]:
dna = "ATCGCGAATTCAC"

In [83]:
if re.search(r"GG(A|T)CC", dna):
    print("restriction site found!")

In [84]:
dna = "ATCGCGAATTCAC"
if re.search(r"GGACC", dna) or re.search(r"GGTCC", dna):
    print("restriction site found!")

In [85]:
dna = "ATCGCGAATTCAC"
if re.search(r"GC[ATGC]GC", dna):
    print("restriction site found!")